In [647]:
from sklearn import datasets
import numpy as np
import pandas as pd
from random import *

iris = datasets.load_iris()
X = iris.data
y = iris.target

In [648]:
def OneHotEncoder(target):
    target_ = []
    
    if isinstance(target, (list, tuple, np.ndarray)):
        for x in range(len(target)):
            if target[x] == 0:
                target_.append([1., 0., 0.])
            if target[x] == 1:
                target_.append([0., 1., 0.])
            if target[x] == 2:
                target_.append([0., 0., 1.])
    else:
        if target == 0:
            target_.append([1., 0., 0.])
        if target == 1:
            target_.append([0., 1., 0.])
        if target == 2:
            target_.append([0., 0., 1.])
            
    return target_   

In [649]:
def generateWeights(data, hiddenLayerNeurons = 5, outputLayerNerons = 3):
    weights = []
    firstRow = data[0][:]
    for x in range(len(firstRow)):
        for i in range(0, hiddenLayerNeurons):
            weights.append(np.random.rand())
            
    for i in range(0, hiddenLayerNeurons):
        for j in range(0, outputLayerNerons):
            weights.append(np.random.rand())
    return weights

def generateWeightsInput(hiddenLayerNeurons, columns, weights, logs = True):
    weightsInputLayer = []
    for w in range(0, hiddenLayerNeurons* columns):
        weightsInputLayer.append(weights[w])
    if logs:        
        print("weights Input Layer: "+ str(len(weightsInputLayer)) + str(weightsInputLayer))    
    return weightsInputLayer

def generateWeightsOutput(hiddenLayerNeurons, outputLayerNeurons, columns, weights, logs = True):
    weightsOutputLayer = []
    for w in range(hiddenLayerNeurons* columns, hiddenLayerNeurons* columns + hiddenLayerNeurons*outputLayerNeurons):
        weightsOutputLayer.append(weights[w])
    if logs:    
        print("weights Output Layer: "+ str(len(weightsOutputLayer)) + str(weightsOutputLayer) ) 
    return weightsOutputLayer

In [650]:
def softmax(Zi, Z):
    exZ = 0
    for i in range(len(Z)):
        exZ += np.exp(Z[i])
    return np.exp(Zi)/ exZ

def sigmoid(x):
    return 1.0/(1.0 + np.exp(-x))
     
def loss(pred, target):
    return (pred - target)**2
    
def derivative_Sigmoid(x):
    return sigmoid(x) * (1 - sigmoid(x))
    
def derivative_loss(pred, target):
    return 2*(pred - target)

def predict(data, weights, threshold = 0.5, bias = 0.20):
    pred = sum(np.array(data) * np.array(weights)) + bias
    return sigmoid(pred)

def cross_entropy(target, output):
     return -np.mean(target * np.log(np.array(output).T + 1e-8))

In [651]:
def updateHiddenLayerSG(hiddenLayerNeurons, outputLayerNeurons, weightsInput, weightsOutput, target, predicted, data, H, columns = 4,  alpha = 0.001, logs = True):

    for j in range(0, hiddenLayerNeurons):
        for i in range(0, columns):
            weightIndex = j * columns + i
            weights_part_two = derivative_Sigmoid(H[i]) * data[i] 
            weightsInput[weightIndex] -= alpha * float(weights_part_two) * np.sum(np.array(weightsOutput[j * outputLayerNeurons:j*outputLayerNeurons + outputLayerNeurons])) 
            if logs:
                print("Updated Input weight number " + str(weightIndex + 1) + " : " + str(weightsInput[weightIndex]))
    return weightsInput

def updateOutputLayerSG(hiddenLayerNeurons, outputLayerNeurons, weightsInput, weightsOutput, target, predicted, data, O, A,  columns = 4,  alpha = 0.001, logs = True):
    
    for j in range(0, outputLayerNeurons):
        for i in range(0, hiddenLayerNeurons):
            weightIndex = j * hiddenLayerNeurons + i
            weightsOutput[weightIndex] -= alpha * (O[j] - target[j]) * A[i] 
            if logs:
                print("Updated Output weight number " + str(weightIndex + 1) + " : " + str(weightsOutput[weightIndex]))
    return weightsOutput

def train_SGD(data, target, weights, hiddenLayerNeurons = 5, outputLayerNeurons = 3, epochs=100, alpha = 0.001, logs = False):
    columns = len(data[0][:])
    
    weightsInputLayer = generateWeightsInput(hiddenLayerNeurons, columns, weights, logs=logs)
    weightsOutputLayer = generateWeightsOutput(hiddenLayerNeurons, outputLayerNeurons, columns, weights, logs =logs)
    
    for epoch in range(epochs):
        if logs:
            print("\n")
            print("Epoch: " + str(epoch))
            
        if logs:
            print("weights: " + str(weights))
        
        for x in range(len(data)): 
            
            H = []
            for j in range (0, hiddenLayerNeurons):
                h = 0
                for p in range (0, columns):
                    h += data[x][p] * np.array(weightsInputLayer[j * columns + p])
                H.append(h)
            if logs:
                print("H: " + str(H)) 

            A = []
            for j in range (0, hiddenLayerNeurons):
                A.append(sigmoid(H[j]))
            if logs:                
                print("A: " + str(A))
        
            predicted = []
            for q in range(0, outputLayerNeurons):
                predicted.append(predict(A, weightsOutputLayer[q*hiddenLayerNeurons:q*hiddenLayerNeurons + hiddenLayerNeurons]))
            if logs:
                print("predicted: " + str(predicted))
            
            H_OUTPUT = []
            for j in range (0, outputLayerNeurons):
                h = 0
                for p in range (0, hiddenLayerNeurons):
                    h += A[p] * np.array(weightsOutputLayer[j * columns + p])
                H_OUTPUT.append(h)
            if logs:
                print("H_OUTPUT: " + str(H_OUTPUT)) 
            
            A_OUTPUT = []
            for j in range (0, outputLayerNeurons):              
                A_OUTPUT.append(softmax(H_OUTPUT[j], H_OUTPUT))
            if logs:
                print("A_OUTPUT: " + str(A_OUTPUT))
            
            #Cross Entropy
            loss_entropy = cross_entropy(target[x], A_OUTPUT)
            if logs:
                print("Loss: " + str(loss_entropy))
            
            weightsOutputLayer = updateOutputLayerSG(hiddenLayerNeurons, outputLayerNeurons, weightsInputLayer, weightsOutputLayer, target[x], predicted, data[x], A_OUTPUT, A, logs = logs)
            weightsInputLayer = updateHiddenLayerSG(hiddenLayerNeurons, outputLayerNeurons, weightsInputLayer, weightsOutputLayer, target[x], predicted, data[x], H, logs=logs)
               
    return weightsOutputLayer,weightsInputLayer

In [652]:
def updateOutputLayer(hiddenLayerNeurons, outputLayerNeurons, weightsInput, weightsOutput, target, predicted, data, O, A,  columns = 4,  alpha = 0.001, logs = True):
    for tar in (target):
        for j in range(0, outputLayerNeurons):
            for i in range(0, hiddenLayerNeurons):
                weightIndex = j * hiddenLayerNeurons + i
                g = (O[:][j] - target[:][j])
                weightsOutput[weightIndex] -= alpha * (np.sum(O[:][j]) - tar[j]) * np.sum(A[:][i])
    if logs:
        for w in range(len(weightsOutput)):        
            print("Updated Output weight number " + str(w + 1) + " : " + str(weightsOutput[w]))
    return weightsOutput

def updateHiddenLayer(hiddenLayerNeurons, outputLayerNeurons, weightsInput, weightsOutput, target, predicted, data, H, columns = 4,  alpha = 0.001, logs = True):
    for input_d in (data):
        for j in range(0, hiddenLayerNeurons):
            for i in range(0, columns):
                weightIndex = j * columns + i
                g_part = np.sum(derivative_Sigmoid(H[i]) * input_d[i]) 
                weightsInput[weightIndex] -= alpha * float(g_part) * np.sum(np.array(weightsOutput[j * outputLayerNeurons:j*outputLayerNeurons + outputLayerNeurons])) 
                                        
    if logs:
        for w in range(len(weightsInput)): 
            print("Updated Input weight number " + str(w + 1) + " : " + str(weightsInput[w]))
    return weightsInput

                                                           
def updateBatchData(weightsInputLayer, weightsOutputLayer, hiddenLayerNeurons, outputLayerNeurons, target, data,  columns = 4,  alpha = 0.001, logs = True):  
        
    H = []
    for x in (data): 
        for j in range (0, hiddenLayerNeurons):
            hDym = []
            h = 0
            for p in range (0, columns):
                h += x[p] * np.array(weightsInputLayer[j * columns + p])
            hDym.append(h)
        H.append(np.array(hDym))
    if logs:
        print("H: " + str(H)) 

    A = []
    for x in (data):
        a = []
        for j in range (0, hiddenLayerNeurons):
            a.append(np.array(sigmoid(H[j])))
        A.append(a)
    if logs:                
        print("A: " + str(A))
    A = np.array(A)
        
    predicted = []
    for x in range (0, len(A)): 
        preds = []
        for q in range(0, outputLayerNeurons):
            preds.append(predict(A, weightsOutputLayer[q*hiddenLayerNeurons:q*hiddenLayerNeurons + hiddenLayerNeurons]))
        predicted.append(preds)
        
    if logs:
        print("predicted: " + str(predicted))

    H_OUTPUT = []
    for x in (data):
        Ho = []
        for j in range (0, outputLayerNeurons):
            h = 0
            for p in range (0, hiddenLayerNeurons):
                h += A[p] * np.array(weightsOutputLayer[j * columns + p])
            Ho.append(h)
        H_OUTPUT.append(Ho)
    if logs:
        print("H_OUTPUT: " + str(H_OUTPUT)) 
            
    A_OUTPUT = []
    for x in (data):
        Ao = []
        for j in range (0, outputLayerNeurons):              
            Ao.append(softmax(H_OUTPUT[j], H_OUTPUT))
        A_OUTPUT.append(Ao)
    if logs:
        print("A_OUTPUT: " + str(A_OUTPUT))
            
    weightsOutputLayer = updateOutputLayer(hiddenLayerNeurons, outputLayerNeurons, weightsInputLayer, weightsOutputLayer, np.array(target[:]), predicted[:], data[:], np.array(A_OUTPUT), np.array(A), logs = logs)
    weightsInputLayer = updateHiddenLayer(hiddenLayerNeurons, outputLayerNeurons, weightsInputLayer, weightsOutputLayer, target[:], predicted[:], data[:], H, logs=logs)

    return weightsOutputLayer, weightsInputLayer

In [676]:
def batchGenarator(data, target, currentBatch,  batchSize =10):
    data_batch = data[currentBatch * batchSize :  batchSize * (currentBatch + 1), :]
    target_batch = np.array(target)[currentBatch * batchSize :  batchSize * (currentBatch + 1), :]
    return data_batch, target_batch

def train_MiniBatchSGD(data, target, weights, batchSize = 10, hiddenLayerNeurons = 5, outputLayerNeurons = 3, epochs=100, alpha = 0.001, logs = False):
    columns = len(data[0][:])
    
    weightsInputLayer = generateWeightsInput(hiddenLayerNeurons, columns, weights, logs=logs)
    weightsOutputLayer = generateWeightsOutput(hiddenLayerNeurons, outputLayerNeurons, columns, weights, logs =logs)
    
    all_batches = data.shape[0] // batchSize 
    if data.shape[0] % batchSize != 0:
        all_batches += 1
        
    if logs:
        print("amount of batches: " + str(all_batches))
    
    for epoch in range(epochs):
        if logs:
            print("\n")
            print("Epoch: " + str(epoch))

        for d_b in range(all_batches):
            if logs:
                print("batch number: " + str(d_b))
            data_batch, target_batch =  batchGenarator(data, target, d_b,  batchSize =batchSize)
            weightsOutputLayer, weightsInputLayer = updateBatchData(weightsInputLayer, weightsOutputLayer, hiddenLayerNeurons, outputLayerNeurons, target_batch, data_batch,  columns = columns, logs = logs)               
    
    return weightsOutputLayer,weightsInputLayer

# TESTING 


# GD

In [677]:
batchSize = 150
target_ = OneHotEncoder(y)
wei = generateWeights(X)
weiOutputs, weiInputs = train_MiniBatchSGD(X, target_, wei.copy(), batchSize = batchSize, epochs=5, alpha = 0.001, logs=True)
weiInputs

weights Input Layer: 20[0.032954447307170565, 0.8383521982599734, 0.5392690924522269, 0.49724653725344126, 0.4121575552555423, 0.27454506859427763, 0.9125975761375852, 0.7216481820346644, 0.860737123509416, 0.41503681083618893, 0.23999858991175216, 0.83374768170635, 0.621848068314539, 0.3548518480546221, 0.16440638635579585, 0.9298321307605931, 0.7095426407761247, 0.37182426526870027, 0.018289036120671676, 0.08291970158225348]
weights Output Layer: 15[0.6963539190649566, 0.9242488352380533, 0.0925386113986072, 0.5911241938727322, 0.07053361746857378, 0.15529520170981637, 0.5952506400694296, 0.20060233516888637, 0.8252714134635738, 0.1596132907053981, 0.022631983496591346, 0.14755273437003724, 0.12223817242183321, 0.6003380060550471, 0.8768479399573192]
amount of batches: 1


Epoch: 0
batch number: 0
H: [array([4.96224099]), array([4.63442033]), array([4.56504775]), array([4.46056886]), array([4.92846915]), array([5.34590414]), array([4.57857921]), array([4.8559332]), array([4.24246658]

H_OUTPUT: [[array([[2.35829763],
       [2.35195759],
       [2.35033366],
       [2.34767   ],
       [2.3577349 ]]), array([[1.83411945],
       [1.82918861],
       [1.82792563],
       [1.82585403],
       [1.8336818 ]]), array([[1.26843208],
       [1.26502204],
       [1.26414859],
       [1.26271592],
       [1.26812941]])], [array([[2.35829763],
       [2.35195759],
       [2.35033366],
       [2.34767   ],
       [2.3577349 ]]), array([[1.83411945],
       [1.82918861],
       [1.82792563],
       [1.82585403],
       [1.8336818 ]]), array([[1.26843208],
       [1.26502204],
       [1.26414859],
       [1.26271592],
       [1.26812941]])], [array([[2.35829763],
       [2.35195759],
       [2.35033366],
       [2.34767   ],
       [2.3577349 ]]), array([[1.83411945],
       [1.82918861],
       [1.82792563],
       [1.82585403],
       [1.8336818 ]]), array([[1.26843208],
       [1.26502204],
       [1.26414859],
       [1.26271592],
       [1.26812941]])], [array([[2.35829763]

A_OUTPUT: [[array([[[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]]]), array([[[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]]]), array([[[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
  

predicted: [[array([[1.        , 1.        , 0.99999998, 1.        , 0.99999944],
       [1.        , 1.        , 0.99999998, 1.        , 0.99999941],
       [1.        , 1.        , 0.99999998, 1.        , 0.99999941],
       [1.        , 1.        , 0.99999998, 1.        , 0.9999994 ],
       [1.        , 1.        , 0.99999998, 1.        , 0.99999943]]), array([[1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.]]), array([[0.99929499, 1.        , 1.        , 1.        , 1.        ],
       [0.9992805 , 1.        , 1.        , 1.        , 1.        ],
       [0.99927678, 1.        , 1.        , 1.        , 1.        ],
       [0.99927048, 1.        , 1.        , 1.        , 1.        ],
       [0.9992937 , 1.        , 1.        , 1.        , 1.        ]])], [array([[1.        , 1.        , 0.99999998, 1.        , 0.99999944],
       [1.        , 1.        , 0.99999998, 1.        , 0.99999941],
      

A_OUTPUT: [[array([[[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]]]), array([[[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]]]), array([[[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
  

...

predicted: [[array([[1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.]]), array([[1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.]]), array([[0.99999954, 1.        , 1.        , 1.        , 1.        ],
       [0.99999952, 1.        , 1.        , 1.        , 1.        ],
       [0.99999951, 1.        , 1.        , 1.        , 1.        ],
       [0.9999995 , 1.        , 1.        , 1.        , 1.        ],
       [0.99999954, 1.        , 1.        , 1.        , 1.        ]])], [array([[1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.]]), array([[1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.]]), array([[0.99999954, 1.        , 1.        , 1.    

A_OUTPUT: [[array([[[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]]]), array([[[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]]]), array([[[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
  

predicted: [[array([[1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.]]), array([[1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.]]), array([[0.99999999, 1.        , 1.        , 1.        , 1.        ],
       [0.99999999, 1.        , 1.        , 1.        , 1.        ],
       [0.99999999, 1.        , 1.        , 1.        , 1.        ],
       [0.99999999, 1.        , 1.        , 1.        , 1.        ],
       [0.99999999, 1.        , 1.        , 1.        , 1.        ]])], [array([[1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.]]), array([[1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1.]]), array([[0.99999999, 1.        , 1.        , 1.    

A_OUTPUT: [[array([[[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]]]), array([[[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]]]), array([[[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667]],

       [[0.00666667],
        [0.00666667],
        [0.00666667],
        [0.00666667],
  

[-0.04065754734463306,
 0.7860455405222457,
 0.4707496897845022,
 0.47302974281780835,
 0.37233477840234186,
 0.2462620285690559,
 0.8755529242982287,
 0.7085555821421552,
 0.7905944683863151,
 0.36519680050797126,
 0.17471088671264748,
 0.8106730743459967,
 0.6003926207167792,
 0.3396276985625388,
 0.14447095305897054,
 0.9227864818538275,
 0.6402181564719094,
 0.3225659618948643,
 -0.04623653867365758,
 0.06011445504028391]

# Mini Batch

In [678]:
batchSize = 15
target_ = OneHotEncoder(y)
wei = generateWeights(X)
weiOutputs, weiInputs = train_MiniBatchSGD(X, target_, wei.copy(), batchSize = batchSize, epochs=5, alpha = 0.001, logs=True)
weiInputs

weights Input Layer: 20[0.9382762261259918, 0.9928073800577832, 0.858279288961328, 0.07140472992415459, 0.8090427697302485, 0.6207687909357074, 0.8511715844921931, 0.7038157057119174, 0.33919375823240916, 0.08068280299957498, 0.21872355555988632, 0.33343863100395277, 0.8649768653441456, 0.32650466625175634, 0.4643902652494638, 0.3353695326264611, 0.6190174898488277, 0.1673229167249427, 0.3774458098681176, 0.7683738187386239]
weights Output Layer: 15[0.478439921139753, 0.29388384644545107, 0.8513358480425924, 0.4705324113199021, 0.635674809861475, 0.08884144676236849, 0.10929111338426478, 0.5254924572042854, 0.44871485982902404, 0.16046281020692432, 0.6551126234183452, 0.7974409865008913, 0.9266354642081474, 0.007882757291815978, 0.15768966019898734]
amount of batches: 10


Epoch: 0
batch number: 0
H: [array([4.4247183]), array([4.21725335]), array([4.08916985]), array([4.08602497]), array([4.37954885]), array([4.94426122]), array([4.17531465]), array([4.38382884]), array([3.89101231]),

H: [array([5.53925479]), array([6.91647654]), array([6.3839555]), array([7.13655765]), array([6.33211237]), array([7.42950262]), array([6.84366234]), array([6.38164612]), array([7.08202967]), array([6.22475899]), array([7.40804492]), array([6.77764746]), array([7.34622052]), array([6.96601029]), array([7.09462125])]
A: [[array([0.99608593]), array([0.99900967]), array([0.99831441]), array([0.99920515]), array([0.99822488])], [array([0.99608593]), array([0.99900967]), array([0.99831441]), array([0.99920515]), array([0.99822488])], [array([0.99608593]), array([0.99900967]), array([0.99831441]), array([0.99920515]), array([0.99822488])], [array([0.99608593]), array([0.99900967]), array([0.99831441]), array([0.99920515]), array([0.99822488])], [array([0.99608593]), array([0.99900967]), array([0.99831441]), array([0.99920515]), array([0.99822488])], [array([0.99608593]), array([0.99900967]), array([0.99831441]), array([0.99920515]), array([0.99822488])], [array([0.99608593]), array([0.99900

        1.30820522e-10]])]]
H_OUTPUT: [[array([[-4.97559051],
       [-4.97319813],
       [-4.97592986],
       [-4.97393538],
       [-4.97536   ]]), array([[-5.88968099],
       [-5.88684909],
       [-5.89008268],
       [-5.88772179],
       [-5.88940813]]), array([[-5.15494806],
       [-5.15246944],
       [-5.15529964],
       [-5.15323327],
       [-5.15470924]])], [array([[-4.97559051],
       [-4.97319813],
       [-4.97592986],
       [-4.97393538],
       [-4.97536   ]]), array([[-5.88968099],
       [-5.88684909],
       [-5.89008268],
       [-5.88772179],
       [-5.88940813]]), array([[-5.15494806],
       [-5.15246944],
       [-5.15529964],
       [-5.15323327],
       [-5.15470924]])], [array([[-4.97559051],
       [-4.97319813],
       [-4.97592986],
       [-4.97393538],
       [-4.97536   ]]), array([[-5.88968099],
       [-5.88684909],
       [-5.89008268],
       [-5.88772179],
       [-5.88940813]]), array([[-5.15494806],
       [-5.15246944],
       [-5.15529

       [-9.06511586]])]]
A_OUTPUT: [[array([[[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]]]), array([[[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]]]), array([[[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],

        [0.06666667]]])]]
Updated Output weight number 1 : -2.8298275743217833
Updated Output weight number 2 : -3.0143836490160876
Updated Output weight number 3 : -2.45693164741894
Updated Output weight number 4 : -2.8377350841416344
Updated Output weight number 5 : -2.672592685600061
Updated Output weight number 6 : -3.2156713192295094
Updated Output weight number 7 : -3.195221652607614
Updated Output weight number 8 : -2.7790203087875973
Updated Output weight number 9 : -2.8557979061628584
Updated Output weight number 10 : -3.144049955784955
Updated Output weight number 11 : -2.8728129525286565
Updated Output weight number 12 : -2.730484589446109
Updated Output weight number 13 : -2.601290111738854
Updated Output weight number 14 : -3.52004281865518
Updated Output weight number 15 : -3.370235915748011
Updated Input weight number 1 : 0.9594427134081035
Updated Input weight number 2 : 1.0029248128046355
Updated Input weight number 3 : 0.8685672348387941
Updated Input weight number 4 

...

        [0.06666667]]])]]
Updated Output weight number 1 : -6.818750881038884
Updated Output weight number 2 : -7.003306955733194
Updated Output weight number 3 : -6.445854954136052
Updated Output weight number 4 : -6.826658390858735
Updated Output weight number 5 : -6.661515992317166
Updated Output weight number 6 : -7.201925677313417
Updated Output weight number 7 : -7.181476010691521
Updated Output weight number 8 : -6.765274666871501
Updated Output weight number 9 : -6.842052264246759
Updated Output weight number 10 : -7.130304313868862
Updated Output weight number 11 : -6.8581526272515845
Updated Output weight number 12 : -6.715824264169041
Updated Output weight number 13 : -6.586629786461789
Updated Output weight number 14 : -7.505382493378108
Updated Output weight number 15 : -7.355575590470939
Updated Input weight number 1 : 1.0332978812405742
Updated Input weight number 2 : 1.0426016506962865
Updated Input weight number 3 : 0.9033296927891654
Updated Input weight number 4 : 0.

A_OUTPUT: [[array([[[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]]]), array([[[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]]]), array([[[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
  

       [-41.19160182]])]]
A_OUTPUT: [[array([[[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]]]), array([[[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]]]), array([[[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667],
        [0.06666667]],

       [[0.06666667],
        [0.06666667],
        [0.06666667]

        [0.06666667]]])]]
Updated Output weight number 1 : -9.265270536309238
Updated Output weight number 2 : -9.449826611003559
Updated Output weight number 3 : -8.892374609406398
Updated Output weight number 4 : -9.273178046129088
Updated Output weight number 5 : -9.108035647587512
Updated Output weight number 6 : -9.647602255699416
Updated Output weight number 7 : -9.627152589077522
Updated Output weight number 8 : -9.210951245257512
Updated Output weight number 9 : -9.287728842632767
Updated Output weight number 10 : -9.575980892254865
Updated Output weight number 11 : -9.153556417640928
Updated Output weight number 12 : -9.011228054558376
Updated Output weight number 13 : -8.882033576851121
Updated Output weight number 14 : -9.80078628376743
Updated Output weight number 15 : -9.650979380860269
Updated Input weight number 1 : 1.0718086535771745
Updated Input weight number 2 : 1.063926389913543
Updated Input weight number 3 : 0.9215512893402972
Updated Input weight number 4 : 0.084

[1.0718467780041165,
 1.0639813995201974,
 0.9217126228380647,
 0.0847395699940608,
 0.9511487306038742,
 0.6964428442376532,
 0.9185614344443145,
 0.7178953471581352,
 0.48745261545382634,
 0.15939965499536513,
 0.2889221484285761,
 0.3479771666291081,
 1.0064164682484484,
 0.40130178219843193,
 0.5315061544295514,
 0.3493952388323767,
 0.7685495317970564,
 0.2464361670304124,
 0.4483977326264249,
 0.783228965092405]

In [656]:
batchSize = 15
target_ = OneHotEncoder(y)
wei = generateWeights(X)
weiOutputs, weiInputs = train_MiniBatchSGD(X, target_, wei.copy(), batchSize = batchSize, epochs=10, alpha = 0.001, logs=False)
weiInputs

[1.0929988906941106,
 0.7803858625780626,
 0.4427625368767538,
 0.37298143883010615,
 0.5743731044844499,
 0.40862158898135564,
 0.2656406923707747,
 0.5859263432840132,
 0.5296551768393782,
 0.7840174358786304,
 0.6367734023791844,
 0.9270868993668424,
 1.067911541078698,
 1.0453668943165966,
 0.9381500356687141,
 0.9051483863575368,
 0.8872505859006874,
 0.6140829414328557,
 0.2661097871759394,
 0.7548836589284497]

In [657]:
target_ = OneHotEncoder(y)
wei = generateWeights(X)
weiOutputs, weiInputs = train_MiniBatchSGD(X, target_, wei.copy(), batchSize = 15, epochs=2, alpha = 0.001, logs=False)

# SGD

In [658]:
target_ = OneHotEncoder(y)
wei = generateWeights(X)
new_weights1, acc1 = train_SGD(X, target_, wei.copy(), epochs=10, alpha = 0.001, logs=True)

weights Input Layer: 20[0.398312620474093, 0.24055894889062057, 0.8927022518891505, 0.4035451039169258, 0.9504057681488386, 0.3491381766200533, 0.8859597758989309, 0.062371422393027065, 0.12511369831378805, 0.36943199072637123, 0.2846465976790721, 0.17043461159201512, 0.46523124021986306, 0.42988840594532907, 0.38895458283234097, 0.5803288905233314, 0.8358100919561077, 0.1748334218730394, 0.4332485901766897, 0.6260134294794448]
weights Output Layer: 15[0.8751101906124765, 0.2628416870528649, 0.14840314749361705, 0.7540536303271547, 0.1969657563431867, 0.16501143069446078, 0.8366434676343365, 0.386456371315108, 0.9048292057992918, 0.8086123798652435, 0.041756555946619756, 0.7723169712568688, 0.7171289680715033, 0.15283655826966025, 0.536110484676309]


Epoch: 0
weights: [0.398312620474093, 0.24055894889062057, 0.8927022518891505, 0.4035451039169258, 0.9504057681488386, 0.3491381766200533, 0.8859597758989309, 0.062371422393027065, 0.12511369831378805, 0.36943199072637123, 0.2846465976790

A_OUTPUT: [0.23751563835888445, 0.26028631344925673, 0.5021980481918589]
Loss: 0.4486576699518044
Updated Output weight number 1 : 0.9085909204548416
Updated Output weight number 2 : 0.29688598280603573
Updated Output weight number 3 : 0.1791763226182739
Updated Output weight number 4 : 0.78768365240314
Updated Output weight number 5 : 0.23088090471023043
Updated Output weight number 6 : 0.1677254497610515
Updated Output weight number 7 : 0.8391901910628738
Updated Output weight number 8 : 0.3894314449884438
Updated Output weight number 9 : 0.9074778585236681
Updated Output weight number 10 : 0.8111949390112365
Updated Output weight number 11 : 0.005561807037664035
Updated Output weight number 12 : 0.735725952075161
Updated Output weight number 13 : 0.6833807192735104
Updated Output weight number 14 : 0.11655788346929834
Updated Output weight number 15 : 0.49961277716327257
Updated Input weight number 1 : 0.39317179479764514
Updated Input weight number 2 : 0.24037800287760921
Updated I

Updated Input weight number 1 : 0.39291522329145845
Updated Input weight number 2 : 0.24037180454926838
Updated Input weight number 3 : 0.865248997949964
Updated Input weight number 4 : 0.40311665352746706
Updated Input weight number 5 : 0.9457874231249974
Updated Input weight number 6 : 0.34897806963843647
Updated Input weight number 7 : 0.8622901342668858
Updated Input weight number 8 : 0.06200292335337221
Updated Input weight number 9 : 0.11664559205589384
Updated Input weight number 10 : 0.36913833597147855
Updated Input weight number 11 : 0.24140392076490066
Updated Input weight number 12 : 0.16976209132139883
Updated Input weight number 13 : 0.45887356465333856
Updated Input weight number 14 : 0.4296677258391162
Updated Input weight number 15 : 0.3574576082376197
Updated Input weight number 16 : 0.5798359259826367
Updated Input weight number 17 : 0.8303572533623826
Updated Input weight number 18 : 0.17464401650776845
Updated Input weight number 19 : 0.40684963260634976
Updated In

Updated Output weight number 4 : 0.8058899456898648
Updated Output weight number 5 : 0.2493716165522491
Updated Output weight number 6 : 0.1636422985654424
Updated Output weight number 7 : 0.8349286007733929
Updated Output weight number 8 : 0.3857739990945539
Updated Output weight number 9 : 0.9033256741702193
Updated Output weight number 10 : 0.8069714697887207
Updated Output weight number 11 : -0.008407258041088387
Updated Output weight number 12 : 0.721367374301282
Updated Output weight number 13 : 0.6714312845116701
Updated Output weight number 14 : 0.10250377453602326
Updated Output weight number 15 : 0.48534553454376983
Updated Input weight number 1 : 0.38757195822329216
Updated Input weight number 2 : 0.24018304054469292
Updated Input weight number 3 : 0.8532876341220702
Updated Input weight number 4 : 0.40289311765395935
Updated Input weight number 5 : 0.9412003593940277
Updated Input weight number 6 : 0.3488160331737863
Updated Input weight number 7 : 0.8519823866274171
Update

A_OUTPUT: [0.23690950428423158, 0.28792965195250914, 0.47516084376325923]
Loss: 0.24803396425710403
Updated Output weight number 1 : 0.9120000715952234
Updated Output weight number 2 : 0.30087191397455204
Updated Output weight number 3 : 0.1809002603085309
Updated Output weight number 4 : 0.7912757309255025
Updated Output weight number 5 : 0.2347385751379063
Updated Output weight number 6 : 0.19495857358335938
Updated Output weight number 7 : 0.8662724148721691
Updated Output weight number 8 : 0.4151717872689184
Updated Output weight number 9 : 0.9345837377749631
Updated Output weight number 10 : 0.8383016408082667
Updated Output weight number 11 : -0.025080467925024698
Updated Output weight number 12 : 0.7046577970973502
Updated Output weight number 13 : 0.6559164393027782
Updated Output weight number 14 : 0.0858599256956419
Updated Output weight number 15 : 0.4686484049385669
Updated Input weight number 1 : 0.386895775401472
Updated Input weight number 2 : 0.24016536523126913
Updated

...

H_OUTPUT: [2.3198933653840585, 1.9395268827969891, 2.981883366108568]
A_OUTPUT: [0.27607095087928524, 0.18872509237547086, 0.5352039567452439]
Loss: 0.20836911949640824
Updated Output weight number 1 : 0.9525763315786694
Updated Output weight number 2 : 0.3472681931485447
Updated Output weight number 3 : 0.2551090918530114
Updated Output weight number 4 : 0.8354991759612916
Updated Output weight number 5 : 0.280067356324689
Updated Output weight number 6 : 0.26324034156305975
Updated Output weight number 7 : 0.9337753525086872
Updated Output weight number 8 : 0.42689164002798824
Updated Output weight number 9 : 0.9999909846122496
Updated Output weight number 10 : 0.9059197179527865
Updated Output weight number 11 : -0.13393849588817008
Updated Output weight number 12 : 0.5907585802868427
Updated Output weight number 13 : 0.5699877549992279
Updated Output weight number 14 : -0.02377076617743642
Updated Output weight number 15 : 0.35570154660726316
Updated Input weight number 1 : 0.27926

Updated Output weight number 4 : 0.8640483436223165
Updated Output weight number 5 : 0.30997303461916514
Updated Output weight number 6 : 0.25043299449263995
Updated Output weight number 7 : 0.9199734486156731
Updated Output weight number 8 : 0.42161204596580865
Updated Output weight number 9 : 0.9869143285859985
Updated Output weight number 10 : 0.8922488464088454
Updated Output weight number 11 : -0.14869954121633638
Updated Output weight number 12 : 0.5743025172946764
Updated Output weight number 13 : 0.5608972693051156
Updated Output weight number 14 : -0.039243277812210285
Updated Output weight number 15 : 0.3394667398567284
Updated Input weight number 1 : 0.24668180197450326
Updated Input weight number 2 : 0.23625149973248125
Updated Input weight number 3 : 0.12649842930192953
Updated Input weight number 4 : 0.37222528748663286
Updated Input weight number 5 : 0.8180154749398211
Updated Input weight number 6 : 0.34538359855295103
Updated Input weight number 7 : 0.2157176421985999


H_OUTPUT: [2.3579023581777707, 1.971183832280473, 2.990033593045284]
A_OUTPUT: [0.2808279796438149, 0.19076146703903413, 0.5284105533171509]
Loss: 0.21262723846536843
Updated Output weight number 1 : 0.9613694866192912
Updated Output weight number 2 : 0.35795813539796795
Updated Output weight number 3 : 0.26886399642063363
Updated Output weight number 4 : 0.8462438913850907
Updated Output weight number 5 : 0.29049225312147975
Updated Output weight number 6 : 0.2836620712152771
Updated Output weight number 7 : 0.9548468662237483
Updated Output weight number 8 : 0.42308157227063165
Updated Output weight number 9 : 1.0185515280588557
Updated Output weight number 10 : 0.9269331042415565
Updated Output weight number 11 : -0.16315338058100956
Updated Output weight number 12 : 0.5589971243223578
Updated Output weight number 13 : 0.5600429181889618
Updated Output weight number 14 : -0.0530760250478407
Updated Output weight number 15 : 0.3242632635217029
Updated Input weight number 1 : 0.221381

Updated Output weight number 6 : 0.2701534386032283
Updated Output weight number 7 : 0.9401834354081469
Updated Output weight number 8 : 0.4205330921267923
Updated Output weight number 9 : 1.005041786018377
Updated Output weight number 10 : 0.9123879922050826
Updated Output weight number 11 : -0.16384761975379394
Updated Output weight number 12 : 0.5569017462211627
Updated Output weight number 13 : 0.5554806731911655
Updated Output weight number 14 : -0.055211363738484086
Updated Output weight number 15 : 0.32232498670480775
Updated Input weight number 1 : 0.18225870825231688
Updated Input weight number 2 : 0.23484871698877577
Updated Input weight number 3 : 0.09328185634374947
Updated Input weight number 4 : 0.35045996672284
Updated Input weight number 5 : 0.7607766192358334
Updated Input weight number 6 : 0.34413804648382645
Updated Input weight number 7 : 0.1862302613224996
Updated Input weight number 8 : 0.015425469283330478
Updated Input weight number 9 : -0.19657723907935823
Upda

A_OUTPUT: [0.27965721069511257, 0.20094336946773966, 0.5193994198371478]
Loss: 0.2183606924959102
Updated Output weight number 1 : 0.9690537577385663
Updated Output weight number 2 : 0.3681013033951626
Updated Output weight number 3 : 0.27815800827971554
Updated Output weight number 4 : 0.8568984965084603
Updated Output weight number 5 : 0.30033490449194866
Updated Output weight number 6 : 0.3024863438453151
Updated Output weight number 7 : 0.9754042296302998
Updated Output weight number 8 : 0.42028585519533423
Updated Output weight number 9 : 1.034800630169418
Updated Output weight number 10 : 0.9473957114040797
Updated Output weight number 11 : -0.18966192433032217
Updated Output weight number 12 : 0.5282965929186122
Updated Output weight number 13 : 0.553544623405178
Updated Output weight number 14 : -0.0799797322817721
Updated Output weight number 15 : 0.29395800498871033
Updated Input weight number 1 : 0.12758552855004032
Updated Input weight number 2 : 0.23378425131422845
Updated